# 1 Import datasets

In [1]:
import pandas as pd 
# load data
confirmed_data = pd.read_csv('time_series_covid19_confirmed_global.csv')
deaths_data = pd.read_csv('time_series_covid19_deaths_global.csv')
recovered_data = pd.read_csv('time_series_covid19_recovered_global.csv')
confirmed_data.head()
#confirmed_data.describe()
#confirmed_data.info()

Province/State Country/Region       Lat       Long  1/22/20  1/23/20  \
0            NaN    Afghanistan  33.93911  67.709953        0        0   
1            NaN        Albania  41.15330  20.168300        0        0   
2            NaN        Algeria  28.03390   1.659600        0        0   
3            NaN        Andorra  42.50630   1.521800        0        0   
4            NaN         Angola -11.20270  17.873900        0        0   

   1/24/20  1/25/20  1/26/20  1/27/20  ...  3/11/21  3/12/21  3/13/21  \
0        0        0        0        0  ...    55917    55959    55959   
1        0        0        0        0  ...   115442   116123   116821   
2        0        0        0        0  ...   114851   115008   115143   
3        0        0        0        0  ...    11130    11199    11228   
4        0        0        0        0  ...    21205    21265    21323   

   3/14/21  3/15/21  3/16/21  3/17/21  3/18/21  3/19/21  3/20/21  
0    55985    55985    55995    56016    56044    56069    56093  
1   117474   118017   118492   118938   119528   120022   120541  
2   115265   115410   115540   115688   115842   115970   116066  
3    11266    11289    11319    11360    11393    11431    11481  
4    21380    21407    21446    21489    21558    21642    21696  

[5 rows x 428 columns]

#  2 Visulization

## 2.1 COVID-19 global situation

In [6]:
from pyecharts import options as opts
from pyecharts.charts import Map, Timeline, Bar, Line
from pyecharts.components import Table
from pyecharts.options import ComponentTitleOpts

lastdate = confirmed_data.columns[-1]
confirmed_total = confirmed_data[lastdate].sum()
deaths_total = deaths_data[lastdate].sum()
recovered_total = recovered_data[lastdate].sum()
deaths_rate = deaths_total / confirmed_total
recovered_rate = recovered_total / confirmed_total

table = Table()

headers = ['Confirmed cases', 'Dead cases', 'Recovered cases', 'Death rate', 'Recovered rate']
rows = [
    [confirmed_total, deaths_total, recovered_total, f'{deaths_rate:.2%}', f'{recovered_rate:.2%}'],    
]
table.add(headers, rows)
table.render_notebook()

In [3]:
confirmed = confirmed_data.groupby('Country/Region').agg({lastdate: 'sum'}).to_dict()[lastdate]
deaths = deaths_data.groupby('Country/Region').agg({lastdate: 'sum'}).to_dict()[lastdate]
recovered = recovered_data.groupby('Country/Region').agg({lastdate: 'sum'}).to_dict()[lastdate]
exists_confirmed = {key: value - deaths[key] - recovered[key]  for key, value in confirmed.items()}
c = (
    Map()
    .add("Confirmed", [*confirmed.items()], "world", is_map_symbol_show=False)
    .add("Recovered", [*recovered.items()], "world", is_map_symbol_show=False)
    .add("Dead", [*deaths.items()], "world", is_map_symbol_show=False)
    .add("Existed confirmed", [*exists_confirmed.items()], "world", is_map_symbol_show=False)
    .set_series_opts(label_opts=opts.LabelOpts(is_show=False))
    .set_global_opts(
        title_opts=opts.TitleOpts(title=f'({lastdate})Global COVID'),
        visualmap_opts=opts.VisualMapOpts(max_=200000),  

    )
)
c.render_notebook()

##  2.2 The spread of COVID-19 confirmed cases globally on map 

In [4]:
# add timeline
tl = Timeline()
tl.add_schema(
       is_loop_play=False,
       play_interval=200,
    )
target = confirmed_data.columns[6:].to_list()
target.reverse()
target = target[::7]
target.reverse()
for dt in target:    
    confirmed = confirmed_data.groupby('Country/Region').agg({dt: 'sum'}).to_dict()[dt]
    c = (
        Map()
        .add("Confirmed cases", [*confirmed.items()], "world", is_map_symbol_show=False)
        .set_series_opts(label_opts=opts.LabelOpts(is_show=False))
        .set_global_opts(
            title_opts=opts.TitleOpts(title="The spread of COVID confirmed cases globally"),
            visualmap_opts=opts.VisualMapOpts(max_=200000),  
            
        )
    )
    tl.add(c, dt)
tl.render_notebook()

### 3.1.3  Top 10 the most confirmed cases by country 

In [5]:
tl = Timeline()
tl.add_schema(
       # is_auto_play=True,
        is_loop_play=False,
        play_interval=100,
    )

for dt in confirmed_data.columns[6:]:
    confirmed = confirmed_data.groupby('Country/Region').agg({dt: 'sum'}).sort_values(by=dt, ascending=False)[:10].sort_values(by=dt).to_dict()[dt]
    bar = (
        Bar()
        .add_xaxis([*confirmed.keys()])
        .add_yaxis("Confirmed cases", [*confirmed.values()], label_opts=opts.LabelOpts(position="right"))
        .reversal_axis()
        .set_global_opts(
            title_opts=opts.TitleOpts("TOP 10 the most confirmed cases by country")
        )
    )
    tl.add(bar, dt)
tl.render_notebook()
